In [28]:
from utils import *

import pandas as pd
import numpy as np
import os

import matplotlib.pyplot as plt
import seaborn as sns
import folium

from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import root_mean_squared_error, accuracy_score

import optuna
from optuna.trial import TrialState

#### Carregando o dataset

In [2]:
df_train = pd.read_csv('../data/treated_data/train.csv')
df_val = pd.read_csv('../data/treated_data/validation.csv')
df_test = pd.read_csv('../data/treated_data/test.csv')

Concatenando os datasets de treino e validação, pois o Random Forest não necessita de validação

In [3]:
df_train = pd.concat([df_train, df_val], ignore_index=False)

In [4]:
df_train.head()

ponto_id  rssi_1_1  rssi_1_2  rssi_1_3  rssi_2_1  rssi_2_2  rssi_2_3  \
0      8790  0.559200  0.398652  0.703014  0.267376  0.426916  0.454187   
1      3227  0.246700  0.000000  0.332592  0.000000  0.360645  0.342995   
2      4180  0.184200  0.000000  0.168521  0.145990  0.318269  0.288125   
3      8922  0.707155  0.446022  0.718534  0.490706  0.361142  0.451422   
4      1117  0.121940  0.157226  0.161643  0.088497  0.252093  0.256320   

   rssi_3_1  rssi_3_2  rssi_3_3   delay_1   delay_2   delay_3       lat  \
0  0.317280  0.311331  0.301273  0.333333  0.571429  0.428571 -8.050090   
1  0.169190  0.339785  0.000000  0.666667  0.428571  0.428571 -8.055834   
2  0.175386  0.277219  0.000000  0.666667  0.428571  0.285714 -8.055424   
3  0.326812  0.331300  0.299672  0.166667  0.571429  0.428571 -8.049530   
4  0.087576  0.252854  0.000000  0.666667  0.428571  0.285714 -8.055380   

         lon  indoor  
0 -34.953120       0  
1 -34.951362       1  
2 -34.951597       1  
3 -34.953290       0  
4 -34.951736       1

In [5]:
X_train = df_train.drop(['ponto_id', 'indoor', 'lat', 'lon'], axis=1).values
y_train = df_train[['lat', 'lon']].values

X_test = df_test.drop(['ponto_id', 'indoor', 'lat', 'lon'], axis=1).values
y_test = df_test[['lat', 'lon']].values

In [6]:
model = RandomForestRegressor(
    n_estimators=10,
    max_depth=10,
    criterion='squared_error',
    min_samples_leaf=1,
    max_features=df_train.shape[1],
    random_state=51
)

In [7]:
model.fit(X=X_train, y=y_train)

RandomForestRegressor(max_depth=10, max_features=16, n_estimators=10,
                      random_state=51)

## Avaliando o modelo

#### Conjunto de Teste

In [8]:
y_pred_test_class = model.predict(X_test)

rmse = np.sqrt(root_mean_squared_error(y_test, y_pred_test_class))
print(f'RMSE: {rmse}')

RMSE: 0.011067194062577203


In [9]:
accuracy = calculate_accuracy(y_pred_test_class, y_test)
print(f"Acurácia: {accuracy:.3f}")


Acurácia: 0.827


In [11]:
map = plot_folium_map(y_test, y_pred_test_class, True)
map

In [12]:
map = plot_folium_map(y_test, y_pred_test_class, False)
map

#### Avaliando o modelos para pontos específicos 

In [13]:
# Prevendo o valor de uma instância específica
idx = 75

X_unit = X_test[idx].reshape(1, -1)
y_unit = np.array([y_test[idx]])
y_pred_unit = model.predict(X_unit)

print(f"Pred Point: {y_pred_unit[0]}")
print(f"Real Point: {y_unit[0]}")

Pred Point: [ -8.055786 -34.951505]
Real Point: [ -8.055786 -34.951505]


In [14]:
map = plot_folium_map(y_unit, y_pred_unit, True)
map

#### Usando o Optune para encontrar os melhores Hiperparâmetros

#### Primeiro iremos criar uma função objetivo, com foco em maximizar o AOC

In [16]:
def objective(trial):

    global x_train
    global y_train

    global X_test
    global y_test
    
    # Sugerir valores para os hiperparâmetros
    n_estimators = trial.suggest_int('n_estimators', 10, 500)
    max_depth = trial.suggest_int('max_depth', 3, 20)
    min_samples_split = trial.suggest_int('min_samples_split', 2, 15)
    min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 10)

    trial.set_user_attr("n_estimators", n_estimators)
    trial.set_user_attr("max_depth", max_depth)
    trial.set_user_attr("min_samples_split", min_samples_split)
    trial.set_user_attr("min_samples_leaf", min_samples_leaf)
    
    # Criar o modelo RandomForest com os hiperparâmetros sugeridos
    model = RandomForestRegressor(
        n_estimators=n_estimators,
        max_depth=max_depth,
        min_samples_split=min_samples_split,
        min_samples_leaf=min_samples_leaf,
        random_state=51,
        criterion='squared_error',
    )

    model.fit(X=X_train, y=y_train)
    
    # Avaliar o modelo usando test k-s
    y_pred_test_class = model.predict(X_test)
    rmse = np.sqrt(root_mean_squared_error(y_test, y_pred_test_class))
    accuracy = calculate_accuracy(y_pred_test_class, y_test)
    
    print(f'\n\nRandom Forest\nn_estimators: {n_estimators}\nmax_depth:{max_depth}\nmin_samples_split:{min_samples_split}\nmin_samples_leaf:{min_samples_leaf}')
    print(f'RMSE: {rmse}\nAccuracy: {accuracy:.3f}')
    

    trial.set_user_attr("RMSE", rmse)
    trial.set_user_attr("Accuracy", accuracy)
    
    return rmse


In [21]:
study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=100)

[I 2024-07-31 19:48:22,865] A new study created in memory with name: no-name-8f3daa1e-3164-45be-a9c1-82cbf5258ab4
[I 2024-07-31 19:48:25,457] Trial 0 finished with value: 0.011645572474963293 and parameters: {'n_estimators': 200, 'max_depth': 8, 'min_samples_split': 2, 'min_samples_leaf': 1}. Best is trial 0 with value: 0.011645572474963293.




Random Forest
n_estimators: 200
max_depth:8
min_samples_split:2
min_samples_leaf:1
RMSE: 0.011645572474963293
Accuracy: 0.620


[I 2024-07-31 19:48:27,840] Trial 1 finished with value: 0.022563810915707236 and parameters: {'n_estimators': 285, 'max_depth': 4, 'min_samples_split': 12, 'min_samples_leaf': 10}. Best is trial 0 with value: 0.011645572474963293.




Random Forest
n_estimators: 285
max_depth:4
min_samples_split:12
min_samples_leaf:10
RMSE: 0.022563810915707236
Accuracy: 0.002


[I 2024-07-31 19:48:29,941] Trial 2 finished with value: 0.022576809933604287 and parameters: {'n_estimators': 260, 'max_depth': 4, 'min_samples_split': 8, 'min_samples_leaf': 5}. Best is trial 0 with value: 0.011645572474963293.


...



Random Forest
n_estimators: 364
max_depth:18
min_samples_split:2
min_samples_leaf:2
RMSE: 0.010250968894755876
Accuracy: 0.848


[I 2024-07-31 19:57:10,489] Trial 98 finished with value: 0.010117466010222908 and parameters: {'n_estimators': 413, 'max_depth': 19, 'min_samples_split': 2, 'min_samples_leaf': 1}. Best is trial 66 with value: 0.010111535094144586.




Random Forest
n_estimators: 413
max_depth:19
min_samples_split:2
min_samples_leaf:1
RMSE: 0.010117466010222908
Accuracy: 0.848


[I 2024-07-31 19:57:17,014] Trial 99 finished with value: 0.010263357441757982 and parameters: {'n_estimators': 452, 'max_depth': 19, 'min_samples_split': 2, 'min_samples_leaf': 2}. Best is trial 66 with value: 0.010111535094144586.




Random Forest
n_estimators: 452
max_depth:19
min_samples_split:2
min_samples_leaf:2
RMSE: 0.010263357441757982
Accuracy: 0.848


#### Salvando os resultados no csv e visualizando os resultados

In [29]:
df = study.trials_dataframe()
df = df[df["state"] == "COMPLETE"].drop(["datetime_start", "datetime_complete", "duration", "state"], axis=1)
df = df.sort_values(['value']) 

csv_file = "optuna_results_rf.csv"
df_existing = pd.read_csv(csv_file) if os.path.isfile(csv_file) else None

df_existing = pd.concat([df_existing, df], ignore_index=True) if df_existing is not None else df
df_existing.to_csv(csv_file, index=False)

In [30]:
df_existing

number     value  params_max_depth  params_min_samples_leaf  \
66      66  0.010112                18                        1   
62      62  0.010115                19                        1   
98      98  0.010117                19                        1   
96      96  0.010120                19                        1   
18      18  0.010122                19                        1   
..     ...       ...               ...                      ...   
1        1  0.022564                 4                       10   
2        2  0.022577                 4                        5   
8        8  0.022683                 4                        5   
78      78  0.028332                 3                        1   
4        4  0.028334                 3                        8   

    params_min_samples_split  params_n_estimators  user_attrs_Accuracy  \
66                         2                  410             0.847788   
62                         2                  417             0.848378   
98                         2                  413             0.847788   
96                         2                  379             0.847788   
18                         2                  438             0.848968   
..                       ...                  ...                  ...   
1                         12                  285             0.002360   
2                          8                  260             0.001770   
8                         11                   71             0.001770   
78                         2                  436             0.149263   
4                          9                   69             0.149263   

    user_attrs_RMSE  user_attrs_max_depth  user_attrs_min_samples_leaf  \
66         0.010112                    18                            1   
62         0.010115                    19                            1   
98         0.010117                    19                            1   
96         0.010120                    19                            1   
18         0.010122                    19                            1   
..              ...                   ...                          ...   
1          0.022564                     4                           10   
2          0.022577                     4                            5   
8          0.022683                     4                            5   
78         0.028332                     3                            1   
4          0.028334                     3                            8   

    user_attrs_min_samples_split  user_attrs_n_estimators  
66                             2                      410  
62                             2                      417  
98                             2                      413  
96                             2                      379  
18                             2                      438  
..                           ...                      ...  
1                             12                      285  
2                              8                      260  
8                             11                       71  
78                             2                      436  
4                              9                       69  

[100 rows x 12 columns]

In [32]:
best_trial = study.best_trials[0]
print("\n-- Best Trial --")
print(f"  RMSE:  {best_trial.user_attrs['RMSE']}")
print(f"  Accuracy: {best_trial.user_attrs['Accuracy']}")

print("  Parameters: ")
for key, val in best_trial.params.items():
    print(f"    {key}: {(16 - len(key)) * ' '}{val}")


print(f"\n-- Overall Results (Ordered by auroc) --")
print(df)

most_important_parameters = optuna.importance.get_param_importances(best_trial)

print("\n-- Most Important Hyperparameters --")
for key, val in most_important_parameters.items():
    print(f"  {key}: {(15 - len(key)) * ' '}{(100 * val):.2f}%")


-- Best Trial --
  RMSE:  0.010111535094144586
  Accuracy: 0.8477876106194691
  Parameters: 
    n_estimators:     410
    max_depth:        18
    min_samples_split: 2
    min_samples_leaf: 1

-- Overall Results (Ordered by auroc) --
    number     value  params_max_depth  params_min_samples_leaf  \
66      66  0.010112                18                        1   
62      62  0.010115                19                        1   
98      98  0.010117                19                        1   
96      96  0.010120                19                        1   
18      18  0.010122                19                        1   
..     ...       ...               ...                      ...   
1        1  0.022564                 4                       10   
2        2  0.022577                 4                        5   
8        8  0.022683                 4                        5   
78      78  0.028332                 3                        1   
4        4  0.028334       

AttributeError: 'FrozenTrial' object has no attribute '_is_multi_objective'